In [ ]:
%%script echo skipping
# remove the magic above to force this block to update your conda environment

%%capture importslog

import sys
%conda install --yes --prefix {sys.prefix} pyyaml
%conda install -c conda-forge --yes --prefix {sys.prefix} atlassian-python-api

import yaml
import atlassian

In [ ]:
# retrieve credentials
import yaml

with open("secrets.yml", 'r') as ymlfile:
    secrets = yaml.safe_load(ymlfile)

assert secrets, "Unable to read expected secrets file for credentials."

In [ ]:
import atlassian

from atlassian import Jira
from atlassian import ServiceDesk

service_desk = ServiceDesk(
    url=secrets['jira']['url'],
    username=secrets['jira']['userid'],
    password=secrets['jira']['token'],
    cloud=True
    )

# service_desk.get_customers(1)
service_desk.get_info()["_links"]["self"]

In [ ]:
ourSD = service_desk.get_service_desk_by_id(
    service_desk.get_service_desks()[0]["id"])

In [ ]:
service_desk.get_customers( service_desk_id=3 )["values"][0]

In [ ]:
import itertools
from typing import Callable, Union

def findSomeCustomersByPredicate(
        predicate: Callable[[str],str], 
        sdId: str,
        sd: ServiceDesk
    ) -> Union[None, dict]:

    # despite pleas otherwise, Jira will only give us 50 records at most
    def getOnePage( pageIndex: int ) -> Union[None, list[dict]]:

        return sd.get_customers( service_desk_id = sdId, start = pageIndex * 50, limit = 50 )[ "values" ]

    # keep fetching pages until we exhaust the collection at the Jira service
    return list( filter( predicate, 
                        itertools.chain.from_iterable( itertools.takewhile( lambda x: x, map( 
                            getOnePage, itertools.count(1) ) ) ) ) )

In [ ]:
import re

customers = sorted( list( map( lambda c: { 'name': c["displayName"], 'email': c["emailAddress"] }, 
                  findSomeCustomersByPredicate( lambda x: re.match( r'^[a-zA-Z0-9._%+-]+@[a-zA-Z0-9.-]+\.[a-zA-Z]{2,}$', x["emailAddress"] ) is not None, "3", service_desk ) ) ),
        key = lambda c: c['name'] )

In [ ]:
import json

json_object = json.dumps(customers, indent=2)
 
with open("customers.json", "w") as outfile:
    outfile.write(json_object)

customers[1]